<img src="logos/geonex_tiles.png" alt="Alt text that describes the graphic" title="Title text" />

# Working with GEONEX Top-of-Atmosphere Reflectance Data

## This tutorial demonstrates how to work with the GO16_ABI05 data product.
*Created: December 6, 2019*

*GeoNEX is a collaborative effort for generating Earth monitoring products from the new generation of geostationary satellite sensors. In collaboration with scientists at NOAA, NASA, and other international organizations, GeoNEX serves as a platform for scientific partnership, knowledge sharing and research for the Earth science community.*

GeoNEX currently offers a gridded top-of-atmosphere, Bidirectional Reflectance Factor data product from the GOES-16, -17 Advanced Baseline Imagers (ABI) and the Advanced Himawari Imager (AHI). The data is available at https://data.nas.nasa.gov/geonex/. We will cover how to download files via the NAS server in this tutorial.

For questions and/or issues with the data products, email support@nas.nasa.gov and include "GeoNEX" in the subject line. You may wish to register with the GeoNEX mailing list geonex@lists.nasa.gov, see https://lists.nasa.gov/mailman/listinfo/geonex/, where community support and data status announcements will be provided.


In this tutorial, we will cover how locate a tile within the GEONEX grid based on a latitude/longitude study site location and how generate a list of files for download based on a given time and date range. Using `wget`, we will download the files from the NAS Data Portal. Next, we will read in the HDF4-EOS files, apply the necessary corrections, and geolocate the rasters. Since the bands are different resolutions, we will interpolate the bands to 1km resolution before calculating NDVI and visualizing NDVI time-series.


### Downloading GEONEX data from NAS Data Portal:
1. [Locate tile in GEONEX Grid based on latitude/longitude site locations](#section1)
2. [Define the date/time range of files for download](#section2)
3. [Generate file names and create a list of files to download](#section3)
4. [Download data from NAS Data Portal](#section4)

### Importing and Interpreting Data
5. [Open a HDF4-EOS File and Read File Metadata](#section5)
6. [Define a function to parse HDF4EOS Metadata](#section6)
7. [Define a function to calculate Lat/Lon](#section7)
8. [Apply Offset, Scale Factor, and Fill value](#section8)
9. [Interpolate bands to 1km](#section9)

### Data Analysis
10. [Calculate NDVI](#section10)
11. [Visualize NDVI Time Series](#section11)




    

<a id='section1'></a>
# Locate tile in GEONEX Grid based on latitude/longitude site locations

### Import libraries

Import the python packages required to complete this tutorial.



In [2]:
#Import necessary libraries
import os
from collections import OrderedDict
from pyhdf.SD import SD, SDC
import xarray as xr
import numpy as np
import pandas as pd
import datetime as dt
import hvplot.xarray 
import geoviews
import scipy
import pyproj
import pprint
from matplotlib import pyplot as plt
from matplotlib.colors import LinearSegmentedColormap
import warnings
warnings.filterwarnings('ignore')

# Add a path to a location to store GEONEX Data
geonex_path = '/Users/camhouser/Documents/GitHub/test'
os.chdir(geonex_path)
# Create a folder for downloads
tutorial_dir = 'geonex_example'
os.makedirs(tutorial_dir, exist_ok=True)
os.chdir(tutorial_dir)



### Download tile boundary text file

This text file includes the latitude and longitude data for each tile. We will use this information to find the tiles that contain our study sites.

In [3]:
# Download the tile boundary text file
!wget -q https://data.nas.nasa.gov/geonex/download_data.php?file=/geonexdata/META/GEONEX_TILES_GLBL.txt -O GEONEX_TILES_GLBL.txt

# Read in file as ndarray, skipping over the header and footer information
geonex_tiles = np.genfromtxt('GEONEX_TILES_GLBL.txt', 
                     skip_header = 7, 
                     skip_footer = 0)   


<a id='section2'></a>

### Download study site locations

For this example, we are going to use the locations of the NSF Neon field sites.

In [4]:
# Download field site locations from NEON
!wget -q https://www.neonscience.org/science-design/field-sites/export/field-sites.csv

# Read field-sites.csv as a pandas dataframe   
neon_field_sites= pd.read_csv('field-sites.csv')

### Define a function that finds the tile that contains our study site locations and returns the vertical and horizontal tile positions

This function loops through our GEO_NEX_TILES_GLBL.txt file information that we read into geonex_tiles to the horizontal (hid) and vertical (vid) tile ids. If the site location falls outside of the GEONEX grid (e.g. a study site in Anchorage, Alaska) the tile ids will be set to `nan`.

In [5]:
def check_tiles(lat,lon,data): 
    in_tile = False
    i = 0
    while(not in_tile): 
        in_tile = lat >= data[i, 4] and lat <= data[i, 5] and lon >= data[i, 2] and lon <= data[i, 3]    
        i += 1
        if i == len(data):
            vid = np.nan
            hid = np.nan
            in_tile = True
        else: 
            hid = '{:02}'.format(int(data[i-1, 0]))
            vid = '{:02}'.format(int(data[i-1, 1]))
    
    return(vid,hid)

### Find tiles

Next we are going to use our check_tiles function within a list comprehension to find the tile for each of our sites. We want to drop duplicate tiles so that we do not download the same file twice if more than one site falls within a tile.

In [6]:
# Create a list of the latitude/longitude sites
sites = list(zip(neon_field_sites['Latitude'],neon_field_sites['Longitude']))

# Find all tile locations
all_tiles = pd.DataFrame([check_tiles(lat,lon,geonex_tiles) for lat,lon in sites],columns=['hid','vid'],dtype=np.int8)

# Add the tiles to our field_site dataframe
field_sites = pd.concat([neon_field_sites,all_tiles],axis=1)

# Find all site locations that do not fall within the geonex grid
no_tile = [sites[missing_site] for missing_site in all_tiles.loc[pd.isnull(all_tiles['vid'])].index]

# Drop duplicate tiles (so you do not download the same tile multiple times!) and NAs
tiles = all_tiles.drop_duplicates().dropna()

# For the sake of this example, let's choose one site to focus on -- Great Smoky Mountains (GRSM)

tiles = field_sites[field_sites['Site ID']=='GRSM'][['hid','vid']]



# If you prefer want to directly specify tiles for download instead of using lat/lon coordinates,
# you can uncomment, update, and run the following line of code.

#tiles =  pd.DataFrame({"vid" : ['04' ,'05', '06'],"hid" : ['07', '08', '09']}) 

<a id='section2'></a>
# Define the date/time range of files for download

### Generate file names for downloading

In this section you will generate the file names for download from the NAS Data portal.


`<Satellite/Sensor Code><ProductID>_<YYYYMMDD>_<HHMM>_GLBG_h<hid>v<vid>_<version>.hdf`

`<Satellite/Sensor Code>`: HM08_AHI for Himawari 8 AHI, and GO16_ABI or GO17_ABI for GOES

`<Product ID>`: A two-digit number assigned to each GeoNEX product. Currently, only the Product ID of “05” is available, indicating “Top-of-Atmosphere Reflectance”

`<YYYYMMDD>`: Year-Month-Day, e.g., 20180501

`<HHMM>`: Hour-Minute (UTC time), e.g., 2030

`<hid>, <vid>`: Horizontal or Vertical Tile ID (0-19)

`<version>`: Product version code. It is currently “02”


### Generate Data and Time Ranges

We can use `datetime` to generate our date and time values for the files we would like to download. The data is provided in 10 minute intervals. To download few and less frequent files, set time_interval value to a multiple of 15.


In [7]:
# Set the start date and time
start_date = '2018-07-16'
start_time = '00:00:00'

# Set the end date and time
end_date = '2018-07-16'
end_time ='23:45:00' 

# Set the time interval (Note: time_interval must be a multiple of 15)
time_interval = '15min' 

# Generate date/time range
date_range = pd.date_range(start = start_date+' '+start_time,end=end_date+' '+end_time,freq=time_interval)

# Format date and time to match file names
date_time = [x.split() for x in date_range.strftime('%Y%m%d %H%M %j %Y').values ]

# Calcuate Day of Year from the dates
doy = date_range.strftime('%j').values

<a id='section3'></a>
# Generate file names and create a list of files to download



In this section, we will combine the sensor and product information with the date/time range to produce a list of files for download.


Below are descriptions of all of the GEONEX antipcated GEONEX data products. **Bold** products are currently available (12/3/2019) through the NAS Data Portal. All products are expected to be released by May 2020. 

* **GOES16/GEONEX-L1B/** 
Top-of-Atmosphere (TOA) reflectance GOES-16 ABI. This product includes the Bidirectional Reflectance Factor (BRF) for Bands 1-6 and Brightness Temperature for Bands 7-16 at the top of the atmosphere measured by the satellite sensor.  BRF is defined as the ratio of the radiance reflected from the target surface (e.g., top of atmosphere) in a particular direction to the expected radiance reflected from a perfectly white Lambertian surface in the same direction under the same conditions of illumination and reflection. The phrase "bidirectional" emphasizes that the variable is a function of both solar incident and satellite-viewing angles. Brightness temperature is the temperature of a blackbody that would emit the same amount of radiation as the targeted body in a specified spectral band. It is different from the true surface temperature because (1) the surface is not a perfect blackbody; and (2) it is influenced by atmospheric conditions. For more information on the steps used to create this product see https://www.nasa.gov/geonex.

* *GOES16/GEONEX-L2/*
GOES16 surface reflectance (Surface BRF) estimated through the process of atmospheric correction for Bands 1-6.SR is calculated by removing the atmospheric influence (absorption and scattering by molecules and aerosols) from the TOA reflectance. The data are also filtered for unfavorable conditions (e.g., clouds and shadows) under which the retrieval of SR is not feasible or reliable.  Intermediate products include cloud masks, atmospheric aerosol optical thickness (AOT), surface BRDF parameters, and so on.

* **GOES16/NOAA-L1B/**
GEONEX GOES16 INPUTS


* **GOES17/GEONEX-L1B/**
Top-of-Atmosphere (TOA) reflectance GOES-17 ABI. Refer to GOES16/GEONEX-L1B/ directory write-up, or the website, for more information.


* *GOES17/GEONEX-L2/*
GOES17 surface reflectance (Surface BRF) estimates. Refer to GOES16/GEONEX-L2/ directory write-up, or the website, for more information.

* **GOES17/NOAA-L1B/**
GEONEX GOES17 INPUTS


* **HIMAWARI8/GEONEX-L1B/**
Top-of-Atmosphere (TOA) reflectance HIMAWARI8. Refer to GOES16/GEONEX-L1B/ directory write-up, or the website, for more information.


* *HIMAWARI8/GEONEX-L2/* 
HIMAWARI8 surface reflectance (Surface BRF) estimates. Refer to GOES16/GEONEX-L2/ directory write-up, or the website, for more information.


* *HIMAWARI8/JMA-L1*
GEONEX HIMAWARI8 INPUTS. See https://www.data.jma.go.jp/mscweb/en/himawari89/space_segment/spsg_sample.html (link valid 2019) for more information.


* **MOTA/MCD12Q1.006/**
This is a convenience dataset which is a GeoNEX tiled MCD12Q1 product. MCD12Q1 is a Terra and Aqua combined Moderate Resolution Imaging Spectroradiometer (MODIS) Land Cover Type (MCD12Q1) data product which provides global land cover types. 
             




In [8]:
# Summary sensor and product information in dictionary
GOES16 = {
    "sensor_code" : "GO16_ABI",
    "products"   : {"GEONEX-L1G" : "05",
    "GEONEX-L2" : "NA",
    "NOAA-L1B" : "NA"}   
}
GOES17 = {
    "sensor_code" : "GO17_ABI",
    "products"   : {"GEONEX-L1G" : "05",
    "GEONEX-L2" : "NA",
    "NOAA-L1B" : "NA"} 
}
HIMAWARI8 = {
    "sensor_code" : "HM08_AHI",
    "products"   : {"GEONEX-L1G" : "05",
    "GEONEX-L2" : "NA",
    "JMA-L1" : "NA"} 
}
geonex_sensors = {
  "GOES16" : GOES16,
  "GOES17" : GOES17,
  "HIMAWARI8" : HIMAWARI8
}

# Select the satellite and product for download
satellite ='GOES16'
product = 'GEONEX-L1G'

# Look up product id and code
product_id = geonex_sensors[satellite]['sensor_code']
product_code = geonex_sensors[satellite]['products'][product]
GLBG = 'GLBG'  # Global Product (only available option)
version = '02' #Current Version

# Create an out directory folder to store the downloaded     
out_dir = os.getcwd()+'/geonex_data'
os.makedirs(out_dir, exist_ok=True)    

Now we can create a function `file_setup` that will:

1. Set up the file directory for the data to be downloaded.
2. Generate the names of the files to be downloaded based on the `datetime` range.
3. Create a `wget` argurments for file downloads.

We are using `wget` which is a free non-interactive commandline tool for retrieving files using HTTP, HTTPS, FTP and FTPS. Here, we generate a script and use a jupyter magic command to run the script via the system command-line.

In [9]:
def file_setup(t,dt):
    # Set up directory structure 
    dir_prefix = '/h'+t[0]+'v'+t[1]+'/'+dt[3]+'/'+dt[2]+'/'
    
    # Create file names
    file_name = product_id+product_code+'_'+dt[0]+'_'+dt[1]+'_'+GLBG+'_h'+t[0]+'v'+t[1]+'_'+version+'.hdf'
    
    # Generate URL 
    url = 'https://data.nas.nasa.gov/geonex/download_data.php?file=/geonexdata/'+satellite+'/'+product+dir_prefix+file_name
    
    # Set up wget command
    wget_call = 'wget -q '+url+' -O '+out_dir+dir_prefix+file_name
    
    # Create folders
    os.makedirs(out_dir+dir_prefix, exist_ok=True)
    return wget_call



<a id='section4'></a>
# Download data from Data Portal


Next, we will use a list comprehension to loop through our `date_time` range for each `tile`.  This ensures that we download all of the tiles over time same time frame. We will write the list to the file `'download_geonex_files.sh'`

In [10]:
# Generate wget calls
file_downloads= [file_setup(t,dt) for dt in date_time for t in tiles.values ]

# Write wget_call list to script file
out_file=open('download_geonex_files.sh','w')
for element in file_downloads:
     out_file.write(element)
     out_file.write('\n')
out_file.close()

Time for some magic! The following line uses the jupyter magic command `!` to run `download_geonex_files.sh` via the command line. This process make take awhile based on the amount of data you are downloading.

In [ ]:
#This takes about 2 minutes
!sh download_geonex_files.sh

## 

<a id='section5'></a>
## Open a HDF4-EOS File and Read File Metadata
Since we know the exact name of all SDS, we can get the data stored in one SDS easily, example with the ABI_B01:

In [11]:

path = os.getcwd()

# Find tile for Great Smoky Mountains (GRSM) field site
h,v = field_sites[field_sites['Site ID']=='GRSM'][['hid','vid']].values[0]


# List all GRSM files
grsm_files =sorted([os.path.join(d, x)
            for d, dirs, files in os.walk(path)
            for x in files if x.endswith(".hdf") and 'h'+h+'v'+v in x])


# Open open file
file = SD(grsm_files[0], SDC.READ)

# See datasets in the file 
datasets_dic = file.datasets()
pprint.pprint(datasets_dic)


{'BAND01': (('YDim:1km GRID', 'XDim:1km GRID'), (600, 600), 23, 2),
 'BAND02': (('YDim:500m GRID', 'XDim:500m GRID'), (1200, 1200), 23, 3),
 'BAND03': (('YDim:1km GRID', 'XDim:1km GRID'), (600, 600), 23, 4),
 'BAND04': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 5),
 'BAND05': (('YDim:1km GRID', 'XDim:1km GRID'), (600, 600), 23, 6),
 'BAND06': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 7),
 'BAND07': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 8),
 'BAND08': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 9),
 'BAND09': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 10),
 'BAND10': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 11),
 'BAND11': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 12),
 'BAND12': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 13),
 'BAND13': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 14),
 'BAND14': (('YDim:2km GRID', 'XDim:2km GRID'), (300, 300), 23, 15),
 'BAND15': (('YDim:2km GRID', 'XDim:2k

<a id='section6'></a>
## Define a function to parse HDF4EOS Metadata

The function below helps to extract the necessary information from the file metadata.

In [12]:
# Define a function to parse HDF4 Metadata
def parse_hdfeos_metadata(string):
    out = OrderedDict()
    lines = [i.replace('\t','') for i in string.split('\n')]
    i = -1
    while i<(len(lines))-1:
        i+=1
        line = lines[i]
        if "=" in line:
            key,value = line.split('=')
            if key in ['GROUP','OBJECT']:
                endIdx = lines.index('END_{}={}'.format(key,value))
                out[value] = parse_hdfeos_metadata("\n".join(lines[i+1:endIdx]))
                i = endIdx
            else:
                if ('END_GROUP' not in key) and ('END_OBJECT' not in key):
                    try:
                        out[key] = eval(value)
                    except NameError:
                        out[key] = str(value)
    return out


<a id='section7'></a>
## Define a function to calculate Lat/Lon

The function below calculates the latitude and longitude for the GEONEX grids.

In [13]:
# Define a function to calculate latitiude and longitude for the tile
def construct_coords(ds,grid):
    out = ds.copy()
    metadata = parse_hdfeos_metadata(ds.attrs['StructMetadata.0'])
    if grid == '500m GRID':
        grid = 'GRID_1'
    if grid == '1km GRID':
        grid = 'GRID_2'
    if grid == '2km GRID':
        grid = 'GRID_3'
    gridInfo = metadata['GridStructure'][grid]
    gridName = gridInfo['GridName']

    x1,y1 = gridInfo['UpperLeftPointMtrs']
    x2,y2 = gridInfo['LowerRightMtrs']
    yRes = (y1-y2)/gridInfo['YDim']
    xRes = (x1-x2)/gridInfo['XDim']

    x = np.arange(x2,x1,xRes)
    y = np.arange(y2,y1,yRes)

    xx,yy = np.meshgrid(x,y)
    
    projStr ="+proj=longlat +datum=WGS84 +no_defs +ellps=WGS84 +towgs84=0,0,0"
    proj = pyproj.Proj(projStr)
    gcs = proj.to_latlong()

    lon,lat = pyproj.transform(proj,gcs,xx,yy)

    ydim,xdim = 'YDim:{}'.format(gridName),'XDim:{}'.format(gridName)
    yCoordName = 'Latitude:{}'.format(gridName)
    xCoordName = 'Longitude:{}'.format(gridName)

    out[yCoordName], out[xCoordName] = ((ydim,xdim),lat),((ydim,xdim),lon)
    return [out[yCoordName]/1e6, out[xCoordName]/1e6] #out.set_coords([yCoordName,xCoordName])





One of the nice features of working with the HDF4-EOS file format is that can access specific band data without having to read in the entire file. Below, we show how to select bands and extract their spatial resolution.

In [14]:
# Let's choose a few bands to work with
bands = ['BAND01','BAND02','BAND03','BAND04','BAND11']

# Notice that there are three different resolutions
grids = []
for b in bands:
    grid = datasets_dic[b][0][0].split(':')[1]
    grids.append(grid)
    
print(grids)

# Remove duplicates for lat/lon calculations
latlon_grids = list(dict.fromkeys(grids))

print(latlon_grids)


['1km GRID', '500m GRID', '1km GRID', '2km GRID', '2km GRID']
['1km GRID', '500m GRID', '2km GRID']


We can read one file and use it to calculate the lat/lon coordinates for the rest of files. We can save the coordinates as dictionary which will allow us to easily apply them to our other files.

In [15]:
# Read in one file using xarray to set up lat/lon 

ds = xr.open_dataset(grsm_files[0])

geo_ds = [construct_coords(ds,g) for g in latlon_grids]

grid_dict = dict(zip(latlon_grids,geo_ds))

<a id='section8'></a>
## Apply Offset, Scale Factor, and Fill value

Since our bands are different resolutions, we will have to interpolate the bands to a matching resolution before we can create a time-series array. The code in the cell below applies the offset and scale factor to the data and assigns the NAN file value before create a DataArray for a time-series each individual band. The data arrays are stored in the `ds_dict` dictionary.

In [16]:
# Since our bands are different resolutions, we are going to begin by

ds_dict = {}
for b in bands:
    band_data = []
    for g in grsm_files: 
        f = SD(g, SDC.READ)
        sds_name = b
        sds_idx = f.nametoindex(sds_name)
        sds_obj = f.select(sds_idx)
        data = sds_obj.get()
        
        data = (data - sds_obj.Offset_Constant)*sds_obj.Scale_Factor
        nan_value = (sds_obj._FillValue - sds_obj.Offset_Constant)*sds_obj.Scale_Factor
        data[data == nan_value]= np.nan
        nan_value = (32768-sds_obj.Offset_Constant)*sds_obj.Scale_Factor
        data[data == nan_value ]= np.nan
        
        data = np.flip(data)
        band_data.append(data)
        sds_obj.endaccess()
        
    grid = datasets_dic[b][0][0].split(':')[1]
    lat = grid_dict[grid][0].values[:,0]
    lon = grid_dict[grid][1].values[0,:]
    
    ds = xr.DataArray(band_data, dims=['time','lat', 'lon'],
                            coords={'lat':lat,
                            'lon': lon,
                            'time': date_range},
                            attrs={'band': b})

    ds_dict[b] = ds    


<a id='section9'></a>
## Interpolate bands to 1km

Now that we have individual data arrays for our bands, we can apply an interpolation method.  Here, we are using the nearest neighbor method available using the `interp_like` function for the xarray library. 

In [17]:

# Interpolate using nearest neighbor --- this takes ~ 1 minute

ds_dict['BAND02_1km'] = ds_dict['BAND02'].interp_like(ds_dict['BAND01'],method='nearest')
ds_dict['BAND04_1km'] = ds_dict['BAND04'].interp_like(ds_dict['BAND01'],method='nearest')
ds_dict['BAND11_1km'] = ds_dict['BAND11'].interp_like(ds_dict['BAND01'],method='nearest')

We can visualize the differences between the original and interpolated bands.

In [18]:
# Plot Initial and Inperpolated Band 11
ds_dict['BAND11'][80].hvplot.quadmesh(cmap='jet', geo=False, rasterize=True,width=400,height=400).relabel('Initial')+\
ds_dict['BAND11_1km'][80].hvplot.quadmesh(cmap='jet', geo=False, rasterize=True,width=400,height=400).relabel('Interpolated')

:Layout
   .DynamicMap.Initial      :DynamicMap   []
      :Image   [lon,lat]   (value)
   .DynamicMap.Interpolated :DynamicMap   []
      :Image   [lon,lat]   (value)

In [19]:
# Now that we have a shared resolution for all of our bands, we can combine the data into an xr dataset
keys = ['BAND01', 'BAND02_1km', 'BAND03', 'BAND04_1km','BAND11_1km']
ds_dict_rs={key:ds_dict[key] for key in keys}
ds = xr.Dataset(ds_dict_rs)
ds = ds

<a id='section10'></a>
## Calculate NDVI

Let's take a look at the Normalized Difference Vegetation Index.

In [20]:
# Calculate NDVI
ds['NDVI'] = (ds['BAND03'] - ds['BAND02_1km'])/(ds['BAND03'] + ds['BAND02_1km'])

# Set values less than 0 to NAN
ds['NDVI'] = ds['NDVI'].where(ds['NDVI']> 0 , drop=True)


We can now easily visualize NDVI for individual times ... 

In [21]:
ds['NDVI'][0].hvplot.quadmesh(cmap='YlGn', geo=False, rasterize=True,width=400,height=400).relabel('NDVI')

:DynamicMap   []
   :Image   [lon,lat]   (NDVI)

Or visualize summary statistics for the entire time-series

*Hint: Change max to std, min, or max to get the standard deviation, the minimum or maximum NDVI for the time-series.*

In [22]:
ds['NDVI'].mean(dim=('time')).hvplot.quadmesh(cmap='YlGn', geo=False, rasterize=True,width=400,height=400).relabel('NDVI')

:DynamicMap   []
   :Image   [lon,lat]   (NDVI)

We can also use latitude and longitude to extract a pixel level time-series for our study site location.

In [23]:
# Get latitude/longitude from our study site of interest
latitude,longitude=field_sites.loc[field_sites['Site ID']=='GRSM',['Latitude','Longitude']].values[0]
# Extract pixel time-series
grsm_ndvi = ds['NDVI'].sel(lon=longitude, lat=latitude, method='nearest')

grsm_ndvi.hvplot.line(x='time', y=['NDVI'], value_label='NDVI at GRSM', legend='top', height=500, width=620)


:Curve   [time]   (NDVI)

We can also visualize the summary statitics for the entire tile as a time-series. The figure below shows the maximum NDVI of the entire tile for each time in our time-series.

In [24]:
ds['NDVI'].max(dim=('lat','lon')).hvplot.line(x='time', y=['NDVI'], 
                value_label='NDVI at GRSM', legend='top', height=600, width=620)

:Curve   [time]   (NDVI)

In addition to NDVI, we can also look at time-series for any of our individual bands.

In [25]:
ds['BAND11_1km'].max(dim=('lat','lon')).hvplot.line(x='time', y=['BAND11_1km'],value_label='B11 at GRSM', legend='top', height=600, width=620)

:Curve   [time]   (BAND11_1km)

## And that's a wrap! We hope you have found this tutorial useful. We are looking forward to seeing all of the exciting work you do with our GEONEX data.